# Read me
This template is meant to be a starter for your customized DREEM output data analysis.

- To install this library, please check the installation on the [Git repo](https://github.com/yvesmartindestaillades/NAP).
- To learn how to use this library, please get through the [tutorial](tutorial.ipynb).


# Your Project Name Here

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib as mpl
from os.path import exists, dirname
import os, sys
import string
import numpy as np
import seaborn as sns
sys.path.append(os.path.abspath(".."))

from nap import *


# Step 1: Data wrangling
### Step 1.1: Define your study and some basics about your project

In [2]:
# Set your root folder in the database (at the moment, keep Yves)
folder = 'Yves'

# Select your study
study = 'tutorial' 

## Set your base coverage high-pass filter value
min_bases_cov = 1000 

# Set the resolution for the plots
mpl.rcParams['figure.dpi'] = 860 # the highest the resolution, the slowest the plotting

# Depending on the study you select, you'll get a series of tubes. You can also create new studies using this dictionary.
# Here's an example.
tubes_per_study = {   
    'tutorial':             ['A6', 'D6'],
    'replicates':           ['C5', 'A4', 'F4', 'A6', 'A7'],
    'salt':                 ['A6', 'B6', 'C6', 'D6', 'E6'], 
    'temperature':          ['D7', 'E7', 'F7', 'G7', 'H7', 'A8', 'B8', 'C8'], 
    'magnesium':            ['F6', 'G6', 'H6', 'A7', 'B7', 'C7'],
    '60 mM DMS kinestics':  ['D8', 'E8', 'F8', 'G8', 'H8', 'A9'],
    'all_tubes': [ele for ele in [f"{a}{b}" for a in string.ascii_uppercase[0:8] for b in range(1,11)] \
                if ele not in ['C3','C10','D10','E10','F10','G10','H10', 'E4']]
                + ['C5_realignment_v3']
    }


conditions_per_study = {
    'temperature': {
        'unit':'C',
        'values':[5, 10, 25, 45, 55, 65, 75, 90]
    },
    '60 mM DMS kinestics': {
        'unit':'min',
        'values':[1, 3, 9, 27, 81]
    },
    'replicates':None,
    'salt':None,
    'magnesium':None,
    'all_tubes':None,
    'tutorial':None
} 

# Define what you will analyse
conditions = conditions_per_study[study]
tubes = tubes_per_study[study]

### Step 1.2: Process new pickle files and push them to Firebase
- Select which tubes you want to push to Firebase.
To plot automatically arrays of tubes, see [tutorial](tutorial.ipynb), section 3.2.
- Process tubes and push them to Firebase.

In [3]:
## Pickle files to process and to push to Firebase
# Can be tubes if you want to process the tubes from your study, or [] if they are already on the database 
pickles_list = [] 
pickles = {pickle: f"../data/FULLSET/{pickle}/mutation_histos.p" for pickle in pickles_list}

# Indicate the location of your RNA structure file
RNAstructureFile = '../data/RNAstructureFile.csv'

# Default location for your local database (JSON file)
json_file = '../data/db.json'

# If the user gives some new pickles files, push them to the firebase, then pull the entire firebase
if len(pickles):
    data_wrangler.push_tubes_to_firebase(pickles = pickles,
                        RNAstructureFile = RNAstructureFile,
                        min_bases_cov = min_bases_cov, 
                        folder=folder)

### Step 1.3: Pull the data from the Firebase and clean/reformat it.
`df` is used for the analysis. Each of the construct have above 1000 reads for each tube.     
`df_full` is used for quality quality analysis. It has all constructs above 1000 valid reads for each tube individually.

In [4]:
# Pull the firebase
df_database = database.load(tubes=tubes, folder=folder)

# Clean and reformat the dataset
df, df_full = data_wrangler.clean_dataset(df_database=df_database,
                                             tubes=tubes)
print(f"{df.groupby('construct')['tubes_covered'].count().count()} constructs have more than {min_bases_cov} reads for each base of their ROI on each tube")

Load data from database
A6 D6 Done!


/home/ymdt/NAP/nap/data_wrangler.py:174: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_full['tubes_covered'].loc[construct[1].index] = construct[1]['sequence'].count()


61 constructs were dropped because deltaG was 'void'
134 constructs have more than 1000 reads for each base of their ROI on each tube


# Step 2: Data quality analysis

It's always hard to realize that you were analysing noise. Here, we'll get through a series a plot to check the data sanity.

### Get the list of tubes and constructs:

In [ ]:
print(f"tubes are: {tubes}")
print(f"constructs are: {df.construct.unique()}")

### Explore the data
`utils.get_roi_info(df=df, tube=tube, construct=construct)` gives information about the ROI of a (tube, construct) pair.

In [5]:
tube, construct = utils.rand_tube_construct(df)
utils.get_roi_info(df=df, tube=tube, construct=construct).xs((True, '0'),level=('paired','roi_structure_comparison'))   

mut_rate  roi_deltaG
base index                      
G    80     0.001197        -9.2
C    81     0.021655        -9.2
A    82     0.018782        -9.2
     83     0.036859        -9.2
T    84     0.006031        -9.2
A    85     0.008136        -9.2
G    86     0.001234        -9.2
     88     0.000248        -9.2
     89     0.000746        -9.2
C    94     0.028006        -9.2
     95     0.009847        -9.2
     96     0.008827        -9.2
T    97      0.00342        -9.2
G    98     0.003166        -9.2
T    99     0.005328        -9.2
     100    0.000801        -9.2
G    101    0.001896        -9.2
C    102    0.004885        -9.2

### Plot the base coverage per construct distribution

In [ ]:
plot.base_coverage_ROI_for_all_constructs(df=df_full)

### Sanity-check (tube, construct)-wise base coverage plots
Plot randomly picked sequences to check the quality of the data.

In [6]:
def random_9_base_coverage(df:pd.DataFrame)->None:
    """Plot the base coverage of 9 randomly picked (tube, construct).

    Args:
        df: a Pandas dataframe.
    """

    random_selection = np.random.randint(len(df), size=(9))
    fig = plt.figure(figsize=(25,25))
    for i in range(9):
        axes1 = plt.subplot(int('33'+str(i+1)))
        plt.plot(np.array(df['cov_bases'].iloc[random_selection[i]]))
        start, end = df['roi_start_index'].iloc[random_selection[i]], df['roi_end_index'].iloc[random_selection[i]]
        plt.plot(np.arange(start, end, 1), np.array(df['cov_bases'].iloc[random_selection[i]])[start:end])
        plt.plot(np.arange(0, len(df['cov_bases'].iloc[random_selection[i]])), len(df['cov_bases'].iloc[random_selection[i]])*[int(df.min_bases_cov.unique())])
        plt.xlabel("Bases")
        plt.ylabel("Coverage")
        plt.title(f"Construct {df['construct'].iloc[random_selection[i]]}, tube {df['tube'].iloc[random_selection[i]]} ")
        plt.grid()
        plt.legend(["Base coverage (all)", 'Base coverage (ROI)', 'min_bases_cov'])
        axes2 = axes1.twinx()   
        axes2.set_ylabel('Coverage [%]')
        axes2.set_ylim((0,100*max(df['cov_bases'].iloc[random_selection[i]]))/df['num_reads'].iloc[random_selection[i]])
    fig.tight_layout()

random_9_base_coverage(df=df)

### Specific (tube, construct) base coverage plot
Plot specified (tube, construct) to check its quality.

In [ ]:
plot.base_coverage(df, tube, construct, min_bases_cov=min_bases_cov, figsize=(15,7))

### Heatmap of the ROI coverage

In [ ]:
plot.heatmap(df = df, 
             column="cov_bases_roi")

### Heatmap of the second half coverage

In [ ]:
plot.heatmap(df = df, 
                column="cov_bases_sec_half")

# Step 3: Data analysis
In this part, we know that we read good data, and we want to visualize it through different plots.

### Analysis parameters

In [ ]:
# Display the plots on this notebook? Not recommended if numerous plots
show_plots = True

# Constructs used
a_few_constructs = df.construct.unique()[:3].tolist()
first_construct = df.construct.unique()[0].tolist()
constructs_per_name = {
    'all_constructs': df.construct.unique().tolist(),
    str(a_few_constructs) : a_few_constructs,
    str(first_construct): [first_construct]
}

# Select constructs here
constructs_name = str(a_few_constructs)

# Define what you will analyse
constructs = constructs_per_name[constructs_name]

### Big script to run every selected function

In [ ]:
# Analysis run in this script
analysis = {'base_per_base_partition':False,
            'base_per_base_sequence': True,
            'deltaG': True,
            'tube_comparison':False,
            'columns_csv': True,
            'deltaG_construct': True
            }


# Write here a script to run all of your plots

### Mutation sequence-wise

`plot.mutation_rate(df, tube, construct, plot_type, index, normalize)` plots the mutation rate base-wise for a given construct of a given tube as a barplot. 
Arguments:
- `plot_type` :
    - `'sequence'` : each bar is colored w.r.t to the base of the original sequence.
    - `'partition'` : each bar shows the partition of into which bases this base mutates.
- `index`:
    - `'index'`: each base is identified with its position number
    - `'base'`: each base is identified with its type (A, C, G, T)

In [ ]:
for construct in constructs:
    for tube in tubes:
        plot.mutation_rate(df=df,
                           tube=tube,
                           construct=construct,
                           plot_type='sequence',
                           index='index')
        plot.save_fig(path=f"data/output/date/{study}/mut_per_base/sequence/{construct}/", 
                    title=f"base_per_base_sequence_{tube}_{construct}")
        plt.close(not show_plots)

### DeltaG plots

In [ ]:
for tube in tubes:
    plot.deltaG(df=df, tube=tube)

    plot.save_fig(path=f"data/output/date/{study}/deltaG/", 
             title=f"deltaG_{tube}")

    plt.close(not show_plots)

### Tubes correlation

In [ ]:
for construct in constructs:
        plot.compare_n_tubes(df, tubes, construct)
        plot.save_fig(path=f"data/output/date/comparison/{study}", 
                      title=f"comparison_{study}_{construct}")
        plt.close(not show_plots)
        print(construct, end=' ')

### Save columns to a csv file

In [ ]:
utils.columns_to_csv(df=df,
                   tubes=tubes,
                   columns=['tube', 'construct','sequence','roi_sequence','mut_bases','info_bases'],
                   title='seq_and_reactivity_{study}',
                   path='data/output/date/{study}'
                   )

### Save construct vs deltaG 

In [ ]:
utils.deltaG_vs_construct_to_csv(df=df, title=f"deltaG_vs_construct.csv", path = f"data/output/date/{study}", tubes=tubes)